In [1]:
import requests
import pandas as pd
from datetime import datetime
from tqdm import tqdm

BINANCE_CANDLE_COLUMNS = ['opentime', 'openprice', 'highprice', 'lowprice', 'closeprice', 'volume', 'closetime',
                          'quotevolume', 'trades', 'taker_buy_volume', 'taker_buy_quote', 'unused']

def binance_recursive_fetch_2(coins, interval, starttime, endtime, data_type='spot'):
    all_coins_result = {}
    data_list = []
    call_dict = {}
    
    for coin in tqdm(coins):
        result_list = []
        current_time = starttime
        call = 0
        timestamps = []
        
        while current_time < endtime:
            if ((int((endtime - current_time) / (1000 * 60))) + 1) >= 1000:
                limit = 1000
            else:
                limit = int((endtime - current_time) / (1000 * 60) + 1)
            
            if data_type == 'spot':
                url = (f'https://api.binance.com/api/v3/klines'
                       f'?symbol={coin}USDT'
                       f'&startTime={str(current_time)}'
                       f'&interval={interval}'
                       f'&limit={str(limit)}')
            elif data_type == 'futures':
                url = (f'https://fapi.binance.com/fapi/v1/klines'
                       f'?symbol={coin}USDT'
                       f'&startTime={str(current_time)}'
                       f'&interval={interval}'
                       f'&limit={str(limit)}')
            
            result_list += requests.get(url).json()
            
            if result_list:
                # Update current_time with the timestamp of the last data point fetched, plus 1 minute (60000 ms)
                current_time = result_list[-1][0] + 60000
                timestamps.append(current_time)
                call += 1
                
                # Check if the last fetched timestamp is greater than or equal to endtime
                if current_time >= endtime:
                    print(f"Reached endtime at {datetime.fromtimestamp(current_time / 1000).strftime('%Y-%m-%d %H:%M:%S')}. Stopping fetch.")
                    break
                
                print((datetime.fromtimestamp(current_time / 1000).strftime('%Y-%m-%d %H:%M:%S')) + 
                      f' status : {current_time < endtime}, time : {current_time}, limit : {call * 2}')
            
            # Ensure there's no continuous fetching of the same timestamp
            if len(timestamps) > 1 and timestamps[-1] == timestamps[-2]:
                print("Duplicate timestamp detected. Stopping fetch.")
                break
            
            # Sleep if needed to avoid rate limiting (adjust based on your rate limit)
            # time.sleep(0.1)  # Uncomment if needed
            
        current_df = pd.DataFrame(result_list, columns=BINANCE_CANDLE_COLUMNS)
        current_df['coin'] = coin
        current_df = current_df[['coin'] + BINANCE_CANDLE_COLUMNS]
        current_df = current_df.values.tolist()
        
        data_list += current_df
        call_dict.update({coin: call})
    
    return {'data': data_list, 'call': call_dict}

# Set endtime to the current time (today)
endtime = int(datetime.utcnow().timestamp() * 1000)

# # Example usage with today's date as the end time
# sample_spot = binance_recursive_fetch_2(
#     ['USDT'],
#     '1m',
#     starttime=int(pd.to_datetime('2023-01-01 00:00', utc=True).timestamp() * 1000),
#     endtime=endtime,
#     data_type='spot'  # Fetch spot data
# )

# print(sample_spot['data'])

/tmp/ipykernel_1079028/3312417040.py:74: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  endtime = int(datetime.utcnow().timestamp() * 1000)


In [14]:
# Fetch NEAR USDT
sample = binance_recursive_fetch_2(
    ['BNB'],
    '1h',
    starttime=int(pd.to_datetime('2000-01-01 00:00', utc=True).timestamp() * 1000),
    endtime=endtime,
    data_type='futures'  # Fetch spot/futures data
)

print(sample['data'])

  0%|          | 0/1 [00:00<?, ?it/s]

2020-03-22 23:01:00 status : True, time : 1584918060000, limit : 2
2020-05-03 15:01:00 status : True, time : 1588518060000, limit : 4
2020-06-14 07:01:00 status : True, time : 1592118060000, limit : 6
2020-07-25 23:01:00 status : True, time : 1595718060000, limit : 8
2020-09-05 15:01:00 status : True, time : 1599318060000, limit : 10
2020-10-17 07:01:00 status : True, time : 1602918060000, limit : 12
2020-11-27 23:01:00 status : True, time : 1606518060000, limit : 14
2021-01-08 15:01:00 status : True, time : 1610118060000, limit : 16
2021-02-19 07:01:00 status : True, time : 1613718060000, limit : 18
2021-04-01 23:01:00 status : True, time : 1617318060000, limit : 20
2021-05-13 15:01:00 status : True, time : 1620918060000, limit : 22
2021-06-24 07:01:00 status : True, time : 1624518060000, limit : 24
2021-08-04 23:01:00 status : True, time : 1628118060000, limit : 26
2021-09-15 15:01:00 status : True, time : 1631718060000, limit : 28
2021-10-27 07:01:00 status : True, time : 1635318060

100%|██████████| 1/1 [00:05<00:00,  5.10s/it]

[['BNB', 1581321600000, '25.070', '25.907', '24.780', '25.053', '302773.53', 1581325199999, '7703234.67716', 6617, '166906.15', '4252310.97583', '0'], ['BNB', 1581325200000, '25.054', '25.054', '24.100', '24.650', '93888.13', 1581328799999, '2305673.24840', 3077, '40071.21', '984049.98637', '0'], ['BNB', 1581328800000, '24.653', '24.898', '24.031', '24.816', '93315.40', 1581332399999, '2283936.47120', 2909, '44478.66', '1088480.94830', '0'], ['BNB', 1581332400000, '24.819', '24.890', '24.262', '24.555', '76560.51', 1581335999999, '1876227.39948', 2239, '37879.11', '927994.63298', '0'], ['BNB', 1581336000000, '24.554', '25.079', '24.380', '24.907', '84379.44', 1581339599999, '2086423.47745', 2360, '44130.95', '1091172.13347', '0'], ['BNB', 1581339600000, '24.893', '25.401', '24.891', '25.048', '134892.72', 1581343199999, '3389155.25738', 3746, '64518.38', '1621382.80166', '0'], ['BNB', 1581343200000, '25.047', '25.200', '24.700', '24.899', '97969.95', 1581346799999, '2444097.30494', 236

In [15]:
# Define the column names for the DataFrame based on the Binance API response structure
columns = ['coin', 'opentime', 'openprice', 'highprice', 'lowprice', 'closeprice', 'volume', 'closetime', 
           'quotevolume', 'trades', 'taker_buy_volume', 'taker_buy_quote', 'unused']

# Convert the list of data into a DataFrame
df = pd.DataFrame(sample['data'], columns=columns)

# Show the first few rows of the DataFrame
df

coin       opentime openprice highprice lowprice closeprice     volume  \
0      BNB  1581321600000    25.070    25.907   24.780     25.053  302773.53   
1      BNB  1581325200000    25.054    25.054   24.100     24.650   93888.13   
2      BNB  1581328800000    24.653    24.898   24.031     24.816   93315.40   
3      BNB  1581332400000    24.819    24.890   24.262     24.555   76560.51   
4      BNB  1581336000000    24.554    25.079   24.380     24.907   84379.44   
...    ...            ...       ...       ...      ...        ...        ...   
42856  BNB  1735603200000   704.750   707.510  702.730    703.450   24577.73   
42857  BNB  1735606800000   703.450   704.800  700.560    702.850   24078.85   
42858  BNB  1735610400000   702.860   707.140  701.940    705.850   19849.77   
42859  BNB  1735614000000   705.850   707.320  702.760    706.550   17461.09   
42860  BNB  1735617600000   706.550   709.760  706.110    706.160   13659.70   

           closetime     quotevolume  trades taker_buy_volume taker_buy_quote  \
0      1581325199999   7703234.67716    6617        166906.15   4252310.97583   
1      1581328799999   2305673.24840    3077         40071.21    984049.98637   
2      1581332399999   2283936.47120    2909         44478.66   1088480.94830   
3      1581335999999   1876227.39948    2239         37879.11    927994.63298   
4      1581339599999   2086423.47745    2360         44130.95   1091172.13347   
...              ...             ...     ...              ...             ...   
42856  1735606799999  17339134.33850   46776         11930.19   8418064.21070   
42857  1735610399999  16915629.63410   43899         12067.22   8476863.43510   
42858  1735613999999  13983981.73790   39619         11317.88   7974768.46340   
42859  1735617599999  12313937.33950   39284          7945.12   5603353.15990   
42860  1735621199999   9672361.10540   18467          6915.07   4898318.01140   

      unused  
0          0  
1          0  
2          0  
3          0  
4          0  
...      ...  
42856      0  
42857      0  
42858      0  
42859      0  
42860      0  

[42861 rows x 13 columns]

In [16]:
# df.to_csv('BNB_USDT_futures_data_2020.csv', index=False)

# print("DataFrame has been saved to csv")

DataFrame has been saved to csv
